In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/malayakew-plant-leaf-dataset/MK/readMe.txt
/kaggle/input/malayakew-plant-leaf-dataset/MK/name_of_spesies.txt
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(8)R225_00163.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(7)R45_00145.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(6)R90_00108.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(5)R225_00097.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(8)R315_00162.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(4)R180_00074.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(7)R180_00141.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(3)R225_00050.jpg
/kaggle/input/malayakew-plant-leaf-dataset/MK/D2/test_patch/Class26/Class26(7)R0_00145.jpg
/kaggle/input/malayakew-plant-leaf-dataset/M

In [ ]:
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
import os
import cv2 as cv
from tqdm.notebook import tqdm_notebook as tqdm
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from keras.models import Sequential,Model
from keras.applications import vgg16,vgg19,resnet
from keras.preprocessing.image import ImageDataGenerator

In [3]:
import os
import numpy as np
from PIL import Image

def load_images(data_path, class_names, target_size=(128,128)):
    images = [
        np.array(Image.open(os.path.join(data_path, class_name, image_filename)).resize(target_size))
        for class_name in class_names
        for image_filename in os.listdir(os.path.join(data_path, class_name))
    ]
    labels = [class_names.index(class_name) for class_name in class_names]
    return np.array(images), np.array(labels)


In [4]:
train_data = '/kaggle/input/malayakew-plant-leaf-dataset/MK/D1/train'
test_data = '/kaggle/input/malayakew-plant-leaf-dataset/MK/D1/test'

In [19]:
selected_folders = ['Class (11)', 'Class (36)']  
X_train, y_train = load_images(train_data, selected_folders)
X_test, y_test = load_images(test_data, selected_folders)

NameError: name 'malaya_kew_plant_leaf' is not defined

In [ ]:
y_train  =np.array(y_train)
X_train = np.array(X_train)
y_test = np.array(y_test)
X_test = np.array(X_test)

In [ ]:
X_train=X_train.astype('float32')/255.0
X_test=X_test.astype('float32')/255.0

In [ ]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator

datagen = ImageDataGenerator(
    rotation_range=30,
    width_shift_range=0.2,
    height_shift_range=0.2,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True,
    fill_mode='constant',
)

def augment_dataset(dataset):
    augmented_data = datagen.flow(dataset, batch_size=len(dataset), shuffle=False)
    return next(augmented_data)  

In [ ]:
X_train_augmented = augment_dataset(X_train)
y_train_augmented = np.repeat(y_train,3, axis=0)  
X_test_augmented = augment_dataset(X_test)
y_test_augmented = np.repeat(y_test,3, axis=0)

In [ ]:
from sklearn.utils import shuffle

X_train_combined = np.concatenate((X_train, X_train_augmented))
y_train_combined = np.concatenate((y_train, y_train_augmented))

X_test_combined = np.concatenate((X_test, X_test_augmented))
y_test_combined = np.concatenate((y_test, y_test_augmented))

In [ ]:
from kerastuner.tuners import RandomSearch
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
from kerastuner.tuners import RandomSearch
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from tensorflow.keras.applications import VGG16,Xception,VGG19,ResNet50
from keras.datasets import cifar10
from keras.applications.vgg16 import preprocess_input
from keras.callbacks import EarlyStopping
from kerastuner.tuners import RandomSearch
import IPython
import kerastuner as kt


In [ ]:
from keras.applications import vgg19
img_rows, img_cols = 224, 224
vgg = vgg19.VGG19(weights = 'imagenet',
                 include_top = False,
                 input_shape = (img_rows, img_cols, 3))

for layer in vgg.layers:
     layer.trainable = False


for (i,layer) in enumerate(vgg.layers):
    print(str(i) + " "+ layer._class.name_, layer.trainable)

In [ ]:
from keras.models import Model
import tensorflow as tf
from keras import backend as K
metrics = [
        'accuracy',
        tf.keras.metrics.AUC(),
        tf.keras.metrics.Recall(),
        tf.keras.metrics.Precision(),
        tf.keras.metrics.F1Score(),
        tf.keras.metrics.SpecificityAtSensitivity(0.5),
        tf.keras.metrics.SensitivityAtSpecificity(0.5),
        tf.keras.metrics.FalseNegatives(),
        tf.keras.metrics.FalsePositives(),
        tf.keras.metrics.TrueNegatives(),
        tf.keras.metrics.TruePositives(),]

In [ ]:
model.compile(optimizer = tf.keras.optimizers.Adam(learning_rate=0.1), loss = 'binary_crossentropy',metrics = metrics)

In [ ]:
callbacks = [
    tf.keras.callbacks.EarlyStopping(
    monitor='val_loss',patience=3,
         restore_best_weights=True,
    )
]
# Train the model
history = model.fit(train_generator, epochs=10, steps_per_epoch=len(train_generator),
                    validation_data=validation_generator, validation_steps=len(validation_generator))

In [ ]:
model.evaluate(X_test,y_test)